# Installing the dependencies

In [ ]:
# !sudo apt-get install -y \
#     libgl1-mesa-dev \
#     libgl1-mesa-glx \
#     libglew-dev \
#     libosmesa6-dev \
#     software-properties-common

# !sudo pt-get install -y patchelf

In [ ]:
# %pip install gym

In [ ]:
# %pip install free-mujoco-py


# Importing the libraries

In [1]:
import mujoco_py
import gym
import numpy as np
import torch
import argparse
import os

import utils
import DDPG

/usr/lib/python3/dist-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.17.3 and <1.25.0 is required for this version of SciPy (detected version 1.26.1
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
/usr/lib/python3/dist-packages/pythran/tables.py:4520: FutureWarning: In the future `np.bool` will be defined as the corresponding NumPy scalar.
  if not hasattr(numpy, method):
/usr/lib/python3/dist-packages/pythran/tables.py:4553: FutureWarning: In the future `np.bytes` will be defined as the corresponding NumPy scalar.
  obj = getattr(themodule, elem)


# Code

In [41]:
# Runs policy for X episodes and returns average reward
# A fixed seed is used for the eval environment
def eval_policy(policy, env_name, seed, eval_episodes=10):
	eval_env = gym.make(env_name)

	avg_reward = 0.
	for _ in range(eval_episodes):
		state = eval_env.reset(seed=seed + 100)[0]
		done = False
		while not done:
			print(state)
			action = policy.select_action(np.array(state))
			print("AAAAAAAAAAAAAAAA")
			print(eval_env.step(action))
			state, reward, done, _, _ = eval_env.step(action)
			avg_reward += reward

	avg_reward /= eval_episodes

	print("---------------------------------------")
	print(f"Evaluation over {eval_episodes} episodes: {avg_reward:.3f}")
	print("---------------------------------------")
	print(avg_reward)
	return avg_reward

In [42]:
ENV = "HalfCheetah-v2"           # OpenAI gym environment name
SEED = 0           # Sets Gym, PyTorch and Numpy seeds
START_TIMESTEPS = 25e3         # Time steps initial random policy is used
EVAL_FREQ = 5e3            # How often (time steps) we evaluate
MAX_TIMESTEPS = 1e6            # Max time steps to run environment
EXPL_NOISE = 0.1         # Std of Gaussian exploration noise
BATCH_SIZE = 256           # Batch size for both actor and critic
DISCOUNT = 0.99          # Discount factor
TAU = 0.005          # Target network update rate
POLICY_NOISE = 0.2           # Noise added to target policy during critic update
NOISE_CLIP = 0.5         # Range to clip target policy noise
POLICY_FREQ = 2            # Frequency of delayed policy updates
SAVE_MODEL = "store_true"         # Save model and optimizer parameters
LOAD_MODEL = ""          # Model load file name, "" doesn't load, "default" uses file_name

In [43]:

env = gym.make(ENV)

# Set seeds
env.action_space.seed(SEED)
torch.manual_seed(SEED)
np.random.seed(SEED)

state_dim = env.observation_space.shape[0]
action_dim = env.action_space.shape[0] 
max_action = float(env.action_space.high[0])

kwargs = {
	"state_dim": state_dim,
	"action_dim": action_dim,
	"max_action": max_action,
	"discount": DISCOUNT,
	"tau": TAU,
}


policy = DDPG.DDPG(**kwargs)

replay_buffer = utils.ReplayBuffer(state_dim, action_dim)

# Evaluate untrained policy
print(policy, ENV, SEED)
print(eval_policy(policy, ENV, SEED,10))
evaluations = [eval_policy(policy, ENV, SEED)]

state, done = env.reset(seed=SEED), False
episode_reward = 0
episode_timesteps = 0
episode_num = 0

for t in range(int(MAX_TIMESTEPS)):
	
	episode_timesteps += 1

	# Select action randomly or according to policy
	if t < START_TIMESTEPS:
		action = env.action_space.sample()
	else:
		action = (
			policy.select_action(np.array(state))
			+ np.random.normal(0, max_action * EXPL_NOISE, size=action_dim)
		).clip(-max_action, max_action)

	# Perform action
	next_state, reward, done, _, _ = env.step(action) 
	done_bool = float(done) if episode_timesteps < env._max_episode_steps else 0

	# Store data in replay buffer
	replay_buffer.add(state, action, next_state, reward, done_bool)

	state = next_state
	episode_reward += reward

	# Train agent after collecting sufficient data
	if t >= START_TIMESTEPS:
		policy.train(replay_buffer, BATCH_SIZE)

	if done: 
		# +1 to account for 0 indexing. +0 on ep_timesteps since it will increment +1 even if done=True
		print(f"Total T: {t+1} Episode Num: {episode_num+1} Episode T: {episode_timesteps} Reward: {episode_reward:.3f}")
		# Reset environment
		state, done = env.reset(seed=SEED), False
		episode_reward = 0
		episode_timesteps = 0
		episode_num += 1 

	# Evaluate episode
	if (t + 1) % EVAL_FREQ == 0:
		evaluations.append(eval_policy(policy, ENV, SEED))
		# np.save(f"./results/{'jonathan'}", evaluations)
		# if SAVE_MODEL: policy.save(f"./models/{'jonathan'}")


AAAAAAAAAAAAAAAA
(array([-1.31909430e-01,  5.94090462e-02,  4.30356338e-02,  4.65382356e-02,
        8.14214190e-03, -8.35470906e-02, -1.58520188e-01, -9.33265258e-02,
        2.12365849e-09, -1.08361956e-09,  2.20060630e-09, -9.50560328e-09,
        6.14161880e-09,  2.57628387e-08,  6.53407861e-09, -1.62459732e-08,
        9.31567396e-09]), -0.0011698603883159798, False, True, {'reward_run': 2.209864791158367e-09, 'reward_ctrl': -0.001169862598180771})
[-1.31909430e-01  5.94090462e-02  4.30356335e-02  4.65382359e-02
  8.14214277e-03 -8.35470904e-02 -1.58520188e-01 -9.33265255e-02
  2.22063127e-09 -1.86596231e-10 -8.33666299e-10 -1.00425659e-10
  3.69043577e-09  1.01542959e-08  1.98381577e-09 -2.01188816e-09
  5.44638721e-09]
AAAAAAAAAAAAAAAA
(array([-1.31909430e-01,  5.94090456e-02,  4.30356353e-02,  4.65382358e-02,
        8.14214020e-03, -8.35470907e-02, -1.58520186e-01, -9.33265261e-02,
        2.15387944e-09,  2.12995788e-09, -1.63431732e-08,  4.41296403e-08,
        1.55962460e-0

KeyboardInterrupt: 